# Simulating Constitutive Processes of semantic change within heterogeneous populations of speakers

In [2]:
# basic imports
import os
import torch
import numpy as np
import pandas as pd
from tqdm.notebook import tqdm

# project code imports
from mod.one_hot_agent import *
from mod.plot import *
from mod.network import *

##### Hyper parameters

In [3]:
model_version = 'sn-1hot-ablated'

In [4]:
no_agents = 20
no_connections = 5
add_vocab_in = 50
semantic_features = 3
starting_observations = 5
starting_uncertainty = .2
words_per_semantic_feature = 5
new_environment_prob = .25
enforce_word_feature_mapping = True

In [5]:
model_path = os.path.join('html',model_version)
if not os.path.exists(model_path):
    os.mkdir(model_path)

## Simple nteraction across repeated turns in a randomly generated environment

In [6]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [7]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [8]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [9]:
# and set the number of iterations
turns = 300

In [10]:
vocab_dif = []

In [11]:
for rd in tqdm(range(turns)):
    env = starting_env.sample()

    net.interaction(env, 3)
    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [12]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [13]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [14]:
fig.write_html(
    os.path.join(model_path,'Randomly-Generated-Environment.html')
)

## Random environment and introduction of new terms

In [15]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [16]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [17]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [18]:
# and set the number of iterations
turns = 300

In [19]:
vocab_dif = []

In [20]:
for rd in tqdm(range(turns)):
    env = starting_env.sample()

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)
    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [21]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [22]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.write_html(
    os.path.join(model_path,'Randomly-Generated-Environment-and-Introducing-Novel-Terms.html')
)
fig.show()

## Changing environment

In [23]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [24]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [25]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [26]:
# and set the number of iterations
turns = 300

In [27]:
vocab_dif = []

In [28]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()

    new_vocab_round = False
    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [29]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [30]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [31]:
fig.write_html(
    os.path.join(model_path,'Suddenly-Changing-Environment.html')
)

## Changing environment and introduction of new terms

In [32]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [33]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [34]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [35]:
# and set the number of iterations
turns = 300

In [36]:
vocab_dif = []

In [37]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)
    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [38]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [39]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [40]:
fig.write_html(
    os.path.join(model_path,'Suddenly-Changing-Environment-and-Introducing-Novel-Terms.html')
)

## Stochastic environment

In [41]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [42]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [43]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [44]:
# and set the number of iterations
turns = 300

In [45]:
vocab_dif = []

In [46]:
for rd in tqdm(range(turns)):

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = False
    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [47]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [48]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [49]:
fig.write_html(
    os.path.join(model_path,'Stochastically-Changing-Environment.html')
)

## Stochastic environment and introduction of new terms

In [50]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [51]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [52]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [53]:
# and set the number of iterations
turns = 30000

In [54]:
vocab_dif = []

In [55]:
for rd in tqdm(range(turns)):

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)
    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/30000 [00:00<?, ?it/s]

In [56]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [57]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [58]:
fig.write_html(
    os.path.join(model_path,'Stochastically-Changing-Environment-and-Introducing-Novel-Terms.html')
)

## Sudden and stochastic environment

In [59]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [60]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [61]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [62]:
# and set the number of iterations
turns = 300

In [63]:
vocab_dif = []

In [64]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = False
    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [65]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [66]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [67]:
fig.write_html(
    os.path.join(model_path,'Suddenly-and-Stochastically-Changing-Environment.html')
)

## Sudden and stochastic environment, plus introduction of new terms

In [68]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [69]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [70]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [71]:
# and set the number of iterations
turns = 300

In [72]:
vocab_dif = []

In [73]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)
    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [74]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [75]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [76]:
fig.write_html(
    os.path.join(model_path,'Suddenly-and-Stochastically-Changing-Environment-and-Introducing-Novel-Terms.html')
)